## Preparing gromacs simulation system
### How-to:
- Look for all TODO statements and check.

In [1]:
%load_ext autoreload
%autoreload 2
%matplotlib inline

In [2]:
from myimports import *

_ColormakerRegistry()

Folder set to   :  gmx_template_for_nmr
Project name    :  gmx_template_for_nmr
SSH host set to : lomo2
GMX cmd set with: module load gromacs/2020.1_nompi
Force field     : amber14sb_parmbsc1_cufix
Force field URL : https://api.github.com/repos/intbio/gromacs_ff/contents/amber14sb_parmbsc1_cufix.ff
Run profile     : lomo2_volta2.sh


In [3]:
display(Markdown(descr))


# MD simulations of NCP with histone tails for NMR parameters calculation 
- AMBER14SB force field
- 150 mM NaCl
- box 2nm


### Check the initial PDB 

In [15]:
np.unique(mda.Universe('wt.pdb').residues.resnames)

array(['ALA', 'ARG', 'ASN', 'ASP', 'CYS', 'DA', 'DC', 'DG', 'DT', 'GLN',
       'GLU', 'GLY', 'HIE', 'HIS', 'ILE', 'LEU', 'LYS', 'MET', 'PHE',
       'PRO', 'SER', 'THR', 'TYR', 'VAL'], dtype=object)

In [10]:
view_nucl('wt.pdb')

NGLWidget()

### We need to specify force field and path to download it from git
- Here we use AMBER 14SB for Gromacs (Need to check)
- In this repo https://github.com/intbio/gromacs_ff/ we store all the forcefield that we check manually or adjust
- Folder for AMBER 14SB ff is amber14sb_parmbsc1.ff 
- Folder for AMBER 14SB ff with CUFIX is amber14sb_parmbsc1_cufix.ff   
- We need to specify a GitHub API URL for it below
- This is now done in config.py

In [4]:
#Set URL here
#Intentianally commented out to make an informed choice
#ff_name='amber14sb_parmbsc1'
# ff_name='amber14sb_parmbsc1_cufix'
# ffurl="https://api.github.com/repos/intbio/gromacs_ff/contents/%s.ff"%ff_name
print("FF set to ",ff_name)

FF set to  amber14sb_parmbsc1_cufix


In [5]:
## Download protocols right away!

In [6]:
%%bash
rm -rf MDProtocols

In [7]:
get_files_from_git(prot_url,'MDProtocols/')

### Prepare directories, download forcefield

In [5]:
%%bash
#clean GMX_system
rm -rf GMX_system
mkdir -p GMX_system

In [6]:
get_files_from_git(ffurl,'GMX_system/%s.ff'%ff_name)

### Let's start with Gromacs commands

- set_gmx_cmd - may be used to alter Gromacs verions depending on the system
- manual for 2018 version is here http://manual.gromacs.org/documentation/current/manual-2018.3.pdf 
- Command line reference http://manual.gromacs.org/documentation/current/user-guide/cmdline.html


### PDB2GMX
- Prepare initial topology (.top), coordinates (.gro) and restrain files .
- http://manual.gromacs.org/documentation/current/onlinehelp/gmx-pdb2gmx.html

In [16]:
%%bash -s "$ff_name" "$set_gmx_cmd" --err err
$2
# TODO: set your input file here the same as output from MD analysis
# PDB2GMX
# Make an init gro file and topology
# Force filed AMBER99BSC1 !!!!!!!!!
# Water TIP3P
# Termini !IMPORTANT! on N-end we place  ACE termini on C-end we place charged group.
# NOTE: The AMBER force fields have unique forms for the terminal residues,
# and these are incompatible with the -ter mechanism.~
# You need to prefix your N- or C-terminal residue names with “N” or “C” respectively
# to use these forms, making sure you preserve the format of the coordinate file.
# Alternatively, use named terminating residues (e.g. ACE, NME).

#NOTE:
#The program has limited intelligence, it reads a number of database files, 
#that allow it to make special bonds (Cys-Cys, Heme-His, etc.), 
#if necessary this can be done manually. The program can prompt the user to select
#which kind of LYS, ASP, GLU, CYS or HIS residue is desired. For Lys the choice is between neutral 
#(two protons on NZ) or protonated (three protons, default), for Asp and Glu unprotonated (default) or 
#protonated, for His the proton can be either on ND1, on NE2 or on both. By default these selections are 
#done automatically. For His, this is based on an optimal hydrogen bonding conformation. Hydrogen bonds 
#are defined based on a simple geometric criterion, specified by the maximum hydrogen-donor-acceptor 
#angle and donor-acceptor distance, which are set by -angle and -dist respectively.
#It is suggested that the user uses interactive options first, i.e. -his and explores the choices by pdb2gmx

cd GMX_system
gmx pdb2gmx -f ../wt.pdb -o init.pdb -p topol.top -i posre.itp -water tip4p -missing -ff $1


Using the Amber14sb_parmbsc1_cufix force field in directory ./amber14sb_parmbsc1_cufix.ff

going to rename ./amber14sb_parmbsc1_cufix.ff/aminoacids.r2b
going to rename ./amber14sb_parmbsc1_cufix.ff/dna.r2b
going to rename ./amber14sb_parmbsc1_cufix.ff/rna.r2b
Reading ../wt.pdb...
Read '', 13569 atoms
Analyzing pdb file
Splitting chemical chains based on TER records or chain id changing.
There are 10 chains and 0 blocks of water and 1264 residues with 13569 atoms

  chain  #res #atoms
  1 'A'   135   1084  
  2 'B'   102    792  
  3 'C'   128    986  
  4 'D'   122    953  
  5 'E'   135   1084  
  6 'F'   102    792  
  7 'G'   128    986  
  8 'H'   122    953  
  9 'I'   145   2952  
  10 'J'   145   2987  

Reading residue database... (Amber14sb_parmbsc1_cufix)
Processing chain 1 'A' (1084 atoms, 135 residues)
Identified residue ALA1 as a starting terminus.
Identified residue ALA135 as a ending terminus.
Checking for duplicate atoms....
Now there are 1073 atoms. Deleted 11 duplica

In [17]:
# Get total charge
for line in err.split('\n'):
    if 'Total charge in system' in line:
        charge=float(line.split()[-2])
print('Total charge is %.3f'%charge)

Total charge is -140.000


## Fixing topol for OPC

In [ ]:
!mkdir -p tmp
!sed s/tip4p.itp/opc.itp/g GMX_system/topol.top > tmp/topol.top
!mv tmp/topol.top GMX_system/topol.top

### Fixing posre.itp files
see this link for details
http://mdsquad.wikia.com/wiki/Change_position_restraint_force_constant_in_MDP

In [12]:
%%bash
cd GMX_system/
for i in posre_*; do
sed -i.bak 's/\(.*\)1000  1000  1000/\1 POSRES_FC POSRES_FC POSRES_FC/g' $i
#check if repaced
tail -n 1 $i
done
rm *.bak



   949     1   POSRES_FC POSRES_FC POSRES_FC
   952     1   POSRES_FC POSRES_FC POSRES_FC
  1546     1   POSRES_FC POSRES_FC POSRES_FC
  1321     1   POSRES_FC POSRES_FC POSRES_FC


### Solvating a molecule
- 2 nm to the border in a cubic box.
- http://manual.gromacs.org/documentation/current/onlinehelp/gmx-editconf.html
- http://manual.gromacs.org/documentation/current/onlinehelp/gmx-solvate.html

In [13]:
%%bash -s "$set_gmx_cmd" --err err
$1
#IMPORTANT NOTE!!!
# The modified vdwradii.dat provided in this repo increases significantly following rafii
# DT   N     0.255
# DC   N     0.255
# DA   N     0.255
# DG   N     0.255
# DT   O     0.255
# DC   O     0.255
# DA   O     0.255
# DG   O     0.255
# AAA  O     0.2
#
#While this allows to avoid clashes with water and system explosion, it significantly lowers the number of water modlecules added!
# For nucleosome this will be 90 000 water mols (non modified) vs 50 000 water molecules for modified

cd GMX_system
cp ../vdwradii.dat .
gmx editconf -bt octahedron -d 2 -c -f init.pdb -o init_box.pdb
gmx solvate -cp init_box.pdb -cs tip4p.gro -o init_solv.pdb -p topol.top
# Sometime with DNA system the water gets inside DNA and the system then explodes
# That's why we use modified vdwradii file here.

Note that major changes are planned in future for editconf, to improve usability and utility.
Read 5682 atoms
Volume: 2101.66 nm^3, corresponds to roughly 945700 electrons
No velocities found
    system size :  6.029  8.458  4.556 (nm)
    diameter    :  9.112               (nm)
    center      :  6.828  9.960  1.295 (nm)
    box vectors : 10.595 18.117 10.949 (nm)
    box angles  :  90.00  90.00  90.00 (degrees)
    box volume  :2101.66               (nm^3)
    shift       :  3.006 -0.126  3.340 (nm)
new center      :  9.834  9.834  4.636 (nm)
new box vectors : 13.112 13.112 13.112 (nm)
new box angles  :  60.00  60.00  90.00 (degrees)
new box volume  :1593.92               (nm^3)

         based on residue and atom names, since they could not be
         definitively assigned from the information in your input
         files. These guessed numbers might deviate from the mass
         and radius of the atom type. Please check the output
         files if necessary.

NOTE: From version 

### Determine the number of ions

- concentration is 150 mM NaCl
- we will calculate the number of waters and calculate the number of ions to add.

In [14]:
for line in err.split('\n'):
    if 'Number of solvent molecules:' in line:
        n_sol=int(line.split()[-1])
print('Amount of solvent molecules: %d'%n_sol)

#Set concentration in mol/liter
conc=0.150 
#Water 18 g/mol. in 1 liter 1000/18 mol
# for every 1000/18 water molecules we need conc of NaCl ion pairs.

n_ions=round(conc*(n_sol/(1000/18)))

if charge>=0:
    n_pos=int(n_ions)
    n_neg=int(n_ions+charge)
else:
    n_pos=int(n_ions-charge)
    n_neg=int(n_ions)
print('Amount of Na %d \nAmount of Cl %d'%(n_pos,n_neg))

Amount of solvent molecules: 26704
Amount of Na 116 
Amount of Cl 72


### Adding ions
- http://manual.gromacs.org/documentation/current/onlinehelp/gmx-grompp.html
- http://manual.gromacs.org/documentation/current/onlinehelp/gmx-genion.html

In [15]:
%%bash -s "$n_pos" "$n_neg" "$set_gmx_cmd"
$3
cd GMX_system
gmx grompp -f ../MDProtocols/ions.mdp -c init_solv.pdb -p topol.top -o ions.tpr -maxwarn 3
gmx genion -s ions.tpr -o init_solv_ions.pdb -p topol.top -noneutral -pname NA -nname CL -np $1 -nn $2 <<!
SOL
!


++++ PLEASE READ AND CITE THE FOLLOWING REFERENCE ++++
J. S. Hub, B. L. de Groot, H. Grubmueller, G. Groenhof
Quantifying Artifacts in Ewald Simulations of Inhomogeneous Systems with a Net
Charge
J. Chem. Theory Comput. 10 (2014) pp. 381-393
-------- -------- --- Thank You --- -------- --------

Analysing residue names:
There are:    60        DNA residues
There are:   174    Protein residues
There are: 27008      Water residues
Analysing Protein...
Calculating fourier grid dimensions for X Y Z
Using a fourier grid of 112x112x112, spacing 0.117 0.117 0.117
This run will generate roughly 7 Mb of data
Will try to add 116 NA ions and 72 CL ions.
Select a continuous group of solvent molecules
Selected 14: 'SOL'

Processing topology
Replacing 188 solute molecules in topology file (topol.top)  by 116 NA and 72 CL ions.


                      :-) GROMACS - gmx grompp, 2020.1 (-:

                            GROMACS is written by:
     Emile Apol      Rossen Apostolov      Paul Bauer     Herman J.C. Berendsen
    Par Bjelkmar      Christian Blau   Viacheslav Bolnykh     Kevin Boyd    
 Aldert van Buuren   Rudi van Drunen     Anton Feenstra       Alan Gray     
  Gerrit Groenhof     Anca Hamuraru    Vincent Hindriksen  M. Eric Irrgang  
  Aleksei Iupinov   Christoph Junghans     Joe Jordan     Dimitrios Karkoulis
    Peter Kasson        Jiri Kraus      Carsten Kutzner      Per Larsson    
  Justin A. Lemkul    Viveca Lindahl    Magnus Lundborg     Erik Marklund   
    Pascal Merz     Pieter Meulenhoff    Teemu Murtola       Szilard Pall   
    Sander Pronk      Roland Schulz      Michael Shirts    Alexey Shvetsov  
   Alfons Sijbers     Peter Tieleman      Jon Vincent      Teemu Virolainen 
 Christian Wennberg    Maarten Wolf      Artem Zhmurov   
                           and the project leaders:
     

### Making index file

http://manual.gromacs.org/documentation/2018/onlinehelp/gmx-make_ndx.html

We also need index that will have a group for non water and ions components

In [16]:
%%bash -s "$set_gmx_cmd"
$1
#The group need to be adjusted!!!
cd GMX_system
gmx make_ndx -f init_solv_ions.pdb -o index.ndx <<!
!"Water_and_ions"
q
!

Going to read 0 old index file(s)
Analysing residue names:
There are:    60        DNA residues
There are:   174    Protein residues
There are: 26820      Water residues
There are:   188        Ion residues
Analysing residues not classified as Protein/DNA/RNA/Water and splitting into groups...
Analysing Protein...
Analysing residues not classified as Protein/DNA/RNA/Water and splitting into groups...

  0 System              : 85418 atoms
  1 DNA                 :  1903 atoms
  2 NA                  :   116 atoms
  3 CL                  :    72 atoms
  4 Protein             :  2867 atoms
  5 Protein-H           :  1394 atoms
  6 C-alpha             :   172 atoms
  7 Backbone            :   518 atoms
  8 MainChain           :   694 atoms
  9 MainChain+Cb        :   855 atoms
 10 MainChain+H         :   863 atoms
 11 SideChain           :  2004 atoms
 12 SideChain-H         :   700 atoms
 13 Prot-Masses         :  2867 atoms
 14 non-Protein         : 82551 atoms
 15 Water               :

                     :-) GROMACS - gmx make_ndx, 2020.1 (-:

                            GROMACS is written by:
     Emile Apol      Rossen Apostolov      Paul Bauer     Herman J.C. Berendsen
    Par Bjelkmar      Christian Blau   Viacheslav Bolnykh     Kevin Boyd    
 Aldert van Buuren   Rudi van Drunen     Anton Feenstra       Alan Gray     
  Gerrit Groenhof     Anca Hamuraru    Vincent Hindriksen  M. Eric Irrgang  
  Aleksei Iupinov   Christoph Junghans     Joe Jordan     Dimitrios Karkoulis
    Peter Kasson        Jiri Kraus      Carsten Kutzner      Per Larsson    
  Justin A. Lemkul    Viveca Lindahl    Magnus Lundborg     Erik Marklund   
    Pascal Merz     Pieter Meulenhoff    Teemu Murtola       Szilard Pall   
    Sander Pronk      Roland Schulz      Michael Shirts    Alexey Shvetsov  
   Alfons Sijbers     Peter Tieleman      Jon Vincent      Teemu Virolainen 
 Christian Wennberg    Maarten Wolf      Artem Zhmurov   
                           and the project leaders:
    

## Making X-ray initial protein file to serve as a reference during analysis

A problem is that gromacs looses info about chain names - which is not good at all and will complicate downstream analysis. So we need to retain it.
init.pdb - still has the correct chain IDs, and since water and ions are added below it can serve for downstream analysis as reference structure.

In [17]:
%%bash 

#--out out
#gmx trjconv -f GMX_system/init_solv.pdb -s GMX_system/ions.tpr -o GMX_system/prot_ref.pdb << !
#1
#!

#Alternative
#gmx editconf -label R E -f GMX_system/init_solv_ions.pdb -n GMX_system/index.ndx -o GMX_system/prot_ref.pdb << !
#1
#!



In [18]:
%%bash -s "$set_gmx_cmd"
$1
##We CANNOT use int_solv_ions - since the chains are renumbered!!!

gmx make_ndx -f GMX_system/init_box.pdb -o GMX_system/index_ref.ndx <<!
"DNA"|"Protein"
q
!
#TODO: you would want only protein and nucleic to be in sys_ref - please, adjust the selection accordingly!!!
#If you PDB does not contain water or ion molecules initially change non-Water to System !!!!
gmx editconf -f GMX_system/init_box.pdb -n GMX_system/index_ref.ndx -o GMX_system/sys_ref.pdb << !
DNA_Protein
!
gmx editconf -f GMX_system/init_box.pdb -n GMX_system/index_ref.ndx -o GMX_system/prot_bb_ref.pdb << !
Backbone
!
gmx editconf -f GMX_system/init_box.pdb -n GMX_system/index_ref.ndx -o GMX_system/prot_bb-h_ref.pdb << !
MainChain+H
!







Going to read 0 old index file(s)
Analysing residue names:
There are:    60        DNA residues
There are:   174    Protein residues
There are:   304      Water residues
Analysing Protein...

  0 System              :  5682 atoms
  1 DNA                 :  1903 atoms
  2 Protein             :  2867 atoms
  3 Protein-H           :  1394 atoms
  4 C-alpha             :   172 atoms
  5 Backbone            :   518 atoms
  6 MainChain           :   694 atoms
  7 MainChain+Cb        :   855 atoms
  8 MainChain+H         :   863 atoms
  9 SideChain           :  2004 atoms
 10 SideChain-H         :   700 atoms
 11 Prot-Masses         :  2867 atoms
 12 non-Protein         :  2815 atoms
 13 Water               :   912 atoms
 14 SOL                 :   912 atoms
 15 non-Water           :  4770 atoms

 nr : group      '!': not  'name' nr name   'splitch' nr    Enter: list groups
 'a': atom       '&': and  'del' nr         'splitres' nr   'l': list residues
 't': atom type  '|': or   'keep' nr     

                     :-) GROMACS - gmx make_ndx, 2020.1 (-:

                            GROMACS is written by:
     Emile Apol      Rossen Apostolov      Paul Bauer     Herman J.C. Berendsen
    Par Bjelkmar      Christian Blau   Viacheslav Bolnykh     Kevin Boyd    
 Aldert van Buuren   Rudi van Drunen     Anton Feenstra       Alan Gray     
  Gerrit Groenhof     Anca Hamuraru    Vincent Hindriksen  M. Eric Irrgang  
  Aleksei Iupinov   Christoph Junghans     Joe Jordan     Dimitrios Karkoulis
    Peter Kasson        Jiri Kraus      Carsten Kutzner      Per Larsson    
  Justin A. Lemkul    Viveca Lindahl    Magnus Lundborg     Erik Marklund   
    Pascal Merz     Pieter Meulenhoff    Teemu Murtola       Szilard Pall   
    Sander Pronk      Roland Schulz      Michael Shirts    Alexey Shvetsov  
   Alfons Sijbers     Peter Tieleman      Jon Vincent      Teemu Virolainen 
 Christian Wennberg    Maarten Wolf      Artem Zhmurov   
                           and the project leaders:
    

As a result in GMX_system directory we have a prepared system for minimization and further simulations.

## Generate pictures of the initial system

In [19]:
!mkdir results
import nglview as nv
from funcs import view_nucl
a=view_nucl('GMX_system/init_solv_ions.pdb',chconv={'A':'C','B':'D','C':'A','D':'B'})
a.add_representation(selection='ion',repr_type='spacefill',opacity=0.9)
a.add_representation(selection='water',repr_type='spacefill',opacity=0.1)
a.add_unitcell()
a._remote_call('setSize',target='Widget',args=['800px','600px'])
a


mkdir: cannot create directory ‘results’: File exists


NGLWidget()

In [20]:
a._remote_call('setSize',target='Widget',args=['800px','600px'])
a.render_image(frame=0,factor=1)
a._display_image()

In [21]:
a._remote_call('setSize',target='Widget',args=['800px','600px'])
a.render_image(frame=0,factor=1)
a._display_image()

In [22]:
import base64
data=str.encode(a._image_data)
with open("results/system_image.png", "wb") as fh:
    fh.write(base64.decodebytes(data))